In [79]:
import datetime
import ast
import json

import numpy as np
import pandas as pd
import string
import re

import matplotlib.pyplot as plt
import seaborn as sns
%matplotlib inline

#from sklearn.model_selection import train_test_split
#from sklearn.ensemble import RandomForestRegressor

#### Read Dataset

In [80]:
df = pd.read_csv('cars.csv')
df.head()

link  \
0  https://www.cars.com/vehicledetail/5ee3ae04-69...   
1  https://www.cars.com/vehicledetail/c99e5035-76...   
2  https://www.cars.com/vehicledetail/4e79fa3a-ba...   
3  https://www.cars.com/vehicledetail/86a0d096-32...   
4  https://www.cars.com/vehicledetail/36efbef5-f2...   

                          listing_title listing_mileage primary_price  \
0      2018 Hyundai Santa Fe Sport 2.4L      79,497 mi.       $17,899   
1                 2017 RAM 1500 Express      80,326 mi.       $27,900   
2                  2019 Nissan Kicks SR      92,959 mi.       $18,950   
3                 2019 RAM 1500 Laramie      59,176 mi.       $39,950   
4  2015 Jeep Wrangler Unlimited Rubicon     135,385 mi.       $26,950   

                  deal_gauge                exterior_color interior_color  \
0         Good Deal $2 under                Nightfall Blue          Beige   
1       This is a good deal.                        Silver          Black   
2  This is a fair deal. Why?  Monarch Orange / Super Black       Charcoal   
3      Great Deal $968 under                          Gray          Black   
4       This is a good deal.                          Blue          Black   

          drivetrain    mpg fuel_type       transmission  \
0  Front-wheel Drive  21-27  Gasoline  6-Speed Automatic   
1   Four-wheel Drive  16-23  Gasoline  8-Speed Automatic   
2  Front-wheel Drive  31-36  Gasoline      Automatic CVT   
3   Four-wheel Drive  19-24  Gasoline  8-Speed Automatic   
4   Four-wheel Drive  16-21  Gasoline                  -   

                  engine                vin stock_number  \
0   2.4L I4 16V GDI DOHC  5XYZT3LB3JG542718        13669   
1   5.7L V8 16V MPFI OHV  3C6RR7KT1HG533082      KBB2955   
2  1.6L I4 16V MPFI DOHC  3N1CP5CU6KL510673      KBB3225   
3   5.7L V8 16V MPFI OHV  1C6SRFDT5KN869809      KBB3246   
4  3.6L V6 24V MPFI DOHC  1C4BJWFG2FL530006      KBB3145   

                                     vehicle_history       seller_name  \
0  {'Accidents or damage': 'None reported', '1-ow...      ETHIO Motors   
1  {'Accidents or damage': 'None reported', '1-ow...  Custom Cars West   
2  {'Accidents or damage': 'None reported', '1-ow...  Custom Cars West   
3  {'Accidents or damage': 'At least 1 accident o...  Custom Cars West   
4  {'Accidents or damage': 'None reported', '1-ow...  Custom Cars West   

                                       price_history  
0  [('9/21/21', 'Listed', '$20,299'), ('2/04/22',...  
1  [('3/15/22', 'Listed', '$30,985'), ('6/01/22',...  
2  [('4/16/22', 'Listed', '$19,980'), ('6/01/22',...  
3  [('6/01/22', 'Listed', '$40,523'), ('7/14/22',...  
4  [('1/21/22', 'Listed', '$29,950'), ('3/22/22',...

## Split vehicle_history to 4 parts 
#### Need to adjust this, to more properly deal with dictionaries

In [92]:
# original code, can remove when confirm that it was properly dealt with

#df[['accident','one_owner','personal_use','open_recall']] = df.vehicle_history.str.split(',',3, expand=True)
#df.head()

def extract_dict(s):
    try:
        # Convert the string to a dictionary using literal_eval
        return ast.literal_eval(s)
    except (SyntaxError, ValueError):
        # Handle cases where literal_eval fails, e.g., malformed strings
        return {}

# First convert dtype to str from object
df['vehicle_history'] = df['vehicle_history'].astype(str)
# Apply the extract_dict fcn
df['vehicle_history'] = df['vehicle_history'].apply(extract_dict)
# normalize and join
norm = pd.json_normalize(df['vehicle_history'])
df = pd.concat([df, norm], axis= 1)
#pd.set_option('display.max_rows', None)
pd.reset_option('display.max_rows')
df

link  \
0  https://www.cars.com/vehicledetail/5ee3ae04-69...   
1  https://www.cars.com/vehicledetail/c99e5035-76...   
2  https://www.cars.com/vehicledetail/4e79fa3a-ba...   
3  https://www.cars.com/vehicledetail/86a0d096-32...   
4  https://www.cars.com/vehicledetail/36efbef5-f2...   

                          listing_title listing_mileage primary_price  \
0      2018 Hyundai Santa Fe Sport 2.4L      79,497 mi.       $17,899   
1                 2017 RAM 1500 Express      80,326 mi.       $27,900   
2                  2019 Nissan Kicks SR      92,959 mi.       $18,950   
3                 2019 RAM 1500 Laramie      59,176 mi.       $39,950   
4  2015 Jeep Wrangler Unlimited Rubicon     135,385 mi.       $26,950   

                  deal_gauge                exterior_color interior_color  \
0         Good Deal $2 under                Nightfall Blue          Beige   
1       This is a good deal.                        Silver          Black   
2  This is a fair deal. Why?  Monarch Orange / Super Black       Charcoal   
3      Great Deal $968 under                          Gray          Black   
4       This is a good deal.                          Blue          Black   

          drivetrain    mpg fuel_type  ...  \
0  Front-wheel Drive  21-27  Gasoline  ...   
1   Four-wheel Drive  16-23  Gasoline  ...   
2  Front-wheel Drive  31-36  Gasoline  ...   
3   Four-wheel Drive  19-24  Gasoline  ...   
4   Four-wheel Drive  16-21  Gasoline  ...   

                      Accidents or damage 1-owner vehicle Personal use only  \
0                           None reported             Yes                No   
1                           None reported              No               Yes   
2                           None reported              No               Yes   
3  At least 1 accident or damage reported              No                No   
4                           None reported              No               Yes   

                       Open recall  Clean title  \
0  At least 1 open recall reported          NaN   
1                              NaN          NaN   
2                              NaN          NaN   
3  At least 1 open recall reported          NaN   
4  At least 1 open recall reported          NaN   

                      Accidents or damage 1-owner vehicle Personal use only  \
0                           None reported             Yes                No   
1                           None reported              No               Yes   
2                           None reported              No               Yes   
3  At least 1 accident or damage reported              No                No   
4                           None reported              No               Yes   

                       Open recall  Clean title  
0  At least 1 open recall reported          NaN  
1                              NaN          NaN  
2                              NaN          NaN  
3  At least 1 open recall reported          NaN  
4  At least 1 open recall reported          NaN  

[5 rows x 30 columns]

In [82]:
df[['year','make','model']] = df.listing_title.str.split(' ',2, expand=True)
df.head()

link  \
0  https://www.cars.com/vehicledetail/5ee3ae04-69...   
1  https://www.cars.com/vehicledetail/c99e5035-76...   
2  https://www.cars.com/vehicledetail/4e79fa3a-ba...   
3  https://www.cars.com/vehicledetail/86a0d096-32...   
4  https://www.cars.com/vehicledetail/36efbef5-f2...   

                          listing_title listing_mileage primary_price  \
0      2018 Hyundai Santa Fe Sport 2.4L      79,497 mi.       $17,899   
1                 2017 RAM 1500 Express      80,326 mi.       $27,900   
2                  2019 Nissan Kicks SR      92,959 mi.       $18,950   
3                 2019 RAM 1500 Laramie      59,176 mi.       $39,950   
4  2015 Jeep Wrangler Unlimited Rubicon     135,385 mi.       $26,950   

                  deal_gauge                exterior_color interior_color  \
0         Good Deal $2 under                Nightfall Blue          Beige   
1       This is a good deal.                        Silver          Black   
2  This is a fair deal. Why?  Monarch Orange / Super Black       Charcoal   
3      Great Deal $968 under                          Gray          Black   
4       This is a good deal.                          Blue          Black   

          drivetrain    mpg fuel_type  ...       seller_name  \
0  Front-wheel Drive  21-27  Gasoline  ...      ETHIO Motors   
1   Four-wheel Drive  16-23  Gasoline  ...  Custom Cars West   
2  Front-wheel Drive  31-36  Gasoline  ...  Custom Cars West   
3   Four-wheel Drive  19-24  Gasoline  ...  Custom Cars West   
4   Four-wheel Drive  16-21  Gasoline  ...  Custom Cars West   

                                       price_history  \
0  [('9/21/21', 'Listed', '$20,299'), ('2/04/22',...   
1  [('3/15/22', 'Listed', '$30,985'), ('6/01/22',...   
2  [('4/16/22', 'Listed', '$19,980'), ('6/01/22',...   
3  [('6/01/22', 'Listed', '$40,523'), ('7/14/22',...   
4  [('1/21/22', 'Listed', '$29,950'), ('3/22/22',...   

                      Accidents or damage 1-owner vehicle Personal use only  \
0                           None reported             Yes                No   
1                           None reported              No               Yes   
2                           None reported              No               Yes   
3  At least 1 accident or damage reported              No                No   
4                           None reported              No               Yes   

                       Open recall Clean title  year     make  \
0  At least 1 open recall reported         NaN  2018  Hyundai   
1                              NaN         NaN  2017      RAM   
2                              NaN         NaN  2019   Nissan   
3  At least 1 open recall reported         NaN  2019      RAM   
4  At least 1 open recall reported         NaN  2015     Jeep   

                        model  
0         Santa Fe Sport 2.4L  
1                1500 Express  
2                    Kicks SR  
3                1500 Laramie  
4  Wrangler Unlimited Rubicon  

[5 rows x 25 columns]

In [83]:
#df = df[['year', 'make', 'model', 'listing_mileage', 'primary_price', 'deal_gauge', 'exterior_color', 'interior_color', 'drivetrain', 'mpg', 'fuel_type', 'transmission', 'engine', 'vin', 'stock_number', 'accident', 'one_owner', 'personal_use', 'open_recall', 'seller_name', 'price_history', 'link']]

## Split price_history to listed_date, price_change, price_change_percentage

In [84]:
# Convert string representation of lists to actual lists
df['price_history'] = df['price_history'].apply(ast.literal_eval)

# Extract the oldest date, total price change, and price change percentage
df['listing_date'] = df['price_history'].apply(lambda x: min([pd.to_datetime(item[0], format='%m/%d/%y')for item in x], default=None))

# Calculate total price change and price change percentage
def calculate_changes(prices):
    if not prices:
        return None, None
    prices = [(pd.to_datetime(date, format='%m/%d/%y'), status, int(price.replace('$', '').replace(',', ''))) for date, status, price in prices]
    total_price_change = prices[-1][2] - prices[0][2]
    price_change_percentage = (total_price_change / prices[0][2]) * 100
    return total_price_change, price_change_percentage

df['total_price_change'], df['price_change_percentage'] = zip(*df['price_history'].apply(calculate_changes))
#pd.set_option('display.max_rows', None)
pd.reset_option('display.max_rows')
df

link  \
0     https://www.cars.com/vehicledetail/5ee3ae04-69...   
1     https://www.cars.com/vehicledetail/c99e5035-76...   
2     https://www.cars.com/vehicledetail/4e79fa3a-ba...   
3     https://www.cars.com/vehicledetail/86a0d096-32...   
4     https://www.cars.com/vehicledetail/36efbef5-f2...   
5     https://www.cars.com/vehicledetail/09f8319c-74...   
6     https://www.cars.com/vehicledetail/1c8bd330-02...   
7     https://www.cars.com/vehicledetail/3a09e54c-1b...   
8     https://www.cars.com/vehicledetail/a76ecc5e-12...   
9     https://www.cars.com/vehicledetail/4e93540c-a4...   
10    https://www.cars.com/vehicledetail/4182da36-7d...   
11    https://www.cars.com/vehicledetail/b0d8920b-e5...   
12    https://www.cars.com/vehicledetail/ec883915-e4...   
13    https://www.cars.com/vehicledetail/123efbf0-a9...   
14    https://www.cars.com/vehicledetail/75a09068-51...   
15    https://www.cars.com/vehicledetail/6e4cc308-e0...   
16    https://www.cars.com/vehicledetail/412d6cbf-8c...   
17    https://www.cars.com/vehicledetail/6a355e69-fa...   
18    https://www.cars.com/vehicledetail/7c1bce9c-a3...   
19    https://www.cars.com/vehicledetail/2e313df1-6e...   
20    https://www.cars.com/vehicledetail/b2cc710b-23...   
21    https://www.cars.com/vehicledetail/23b79a86-dd...   
22    https://www.cars.com/vehicledetail/75f8c9b4-cd...   
23    https://www.cars.com/vehicledetail/9a08a368-68...   
24    https://www.cars.com/vehicledetail/3c884797-89...   
25    https://www.cars.com/vehicledetail/91f0edb9-be...   
26    https://www.cars.com/vehicledetail/d92b1fa8-a9...   
27    https://www.cars.com/vehicledetail/c8bd5932-e4...   
28    https://www.cars.com/vehicledetail/5af236ce-aa...   
29    https://www.cars.com/vehicledetail/69f675f2-a4...   
30    https://www.cars.com/vehicledetail/43592b4e-18...   
31    https://www.cars.com/vehicledetail/0f9198c2-e0...   
32    https://www.cars.com/vehicledetail/4c4270a4-bf...   
33    https://www.cars.com/vehicledetail/16b7bea0-e2...   
34    https://www.cars.com/vehicledetail/6820ad3d-ea...   
35    https://www.cars.com/vehicledetail/4ce7a4ef-4e...   
36    https://www.cars.com/vehicledetail/88b5d18a-2c...   
37    https://www.cars.com/vehicledetail/2acffbbc-2c...   
38    https://www.cars.com/vehicledetail/ac709e70-4b...   
39    https://www.cars.com/vehicledetail/441e1113-5c...   
40    https://www.cars.com/vehicledetail/52a8b703-cc...   
41    https://www.cars.com/vehicledetail/1545e9d6-1f...   
42    https://www.cars.com/vehicledetail/80fcbdd1-27...   
43    https://www.cars.com/vehicledetail/a5a66ac4-e1...   
44    https://www.cars.com/vehicledetail/65ff5600-bd...   
45    https://www.cars.com/vehicledetail/20dea996-d3...   
46    https://www.cars.com/vehicledetail/efe34872-70...   
47    https://www.cars.com/vehicledetail/d3357937-2e...   
48    https://www.cars.com/vehicledetail/be059850-f3...   
49    https://www.cars.com/vehicledetail/d4fb6c96-79...   
50    https://www.cars.com/vehicledetail/e15d4d4f-7c...   
51    https://www.cars.com/vehicledetail/b759a787-a8...   
52    https://www.cars.com/vehicledetail/1a4efd84-ba...   
53    https://www.cars.com/vehicledetail/6d3c4dce-c4...   
54    https://www.cars.com/vehicledetail/9cdd5486-fd...   
55    https://www.cars.com/vehicledetail/bc519869-f4...   
56    https://www.cars.com/vehicledetail/dd86b6bf-bf...   
57    https://www.cars.com/vehicledetail/99efe37a-e1...   
58    https://www.cars.com/vehicledetail/c8fb2cf1-82...   
59    https://www.cars.com/vehicledetail/056c8b5a-0b...   
60    https://www.cars.com/vehicledetail/20f800b5-cd...   
61    https://www.cars.com/vehicledetail/f3734092-4d...   
62    https://www.cars.com/vehicledetail/e6b39ac8-f0...   
63    https://www.cars.com/vehicledetail/c2532d31-f7...   
64    https://www.cars.com/vehicledetail/9e0b37c7-5a...   
65    https://www.cars.com/vehicledetail/9978bc29-80...   
66    https://www.cars.com/vehicledetail/ea6060db-ed...   
67    https://www.cars.com/vehicledetai

In [85]:
df.shape

(6002, 28)

In [86]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 6002 entries, 0 to 6001
Data columns (total 28 columns):
 #   Column                   Non-Null Count  Dtype         
---  ------                   --------------  -----         
 0   link                     6002 non-null   object        
 1   listing_title            6002 non-null   object        
 2   listing_mileage          6002 non-null   object        
 3   primary_price            6002 non-null   object        
 4   deal_gauge               5524 non-null   object        
 5   exterior_color           6002 non-null   object        
 6   interior_color           6002 non-null   object        
 7   drivetrain               6002 non-null   object        
 8   mpg                      5957 non-null   object        
 9   fuel_type                6002 non-null   object        
 10  transmission             6002 non-null   object        
 11  engine                   6002 non-null   object        
 12  vin                      6002 non-

In [87]:
# Check unique values to see what we're working with: 
# engine, transmission, drivetrain. 
# might need to standardize for the model to use.

unique_engines = sorted(df['engine'].unique())
unique_transmissions = sorted(df['transmission'].unique())
unique_drivetrains = sorted(df['drivetrain'].unique())
unique_fuel_types = sorted(df['fuel_type'].unique())

# Print the unique values
print("Sorted Unique Engines:")
for engine in unique_engines:
    print(engine)
# Want to isolate: 
# cylinders
# liters
# boosted ("Turbo"/"Supercharge") T/F

print("\nSorted Unique Transmissions:")
for transmission in unique_transmissions:
    print(transmission)
# Not worth the effort to differentiate automatic versus manual

print("\nSorted Unique Drivetrains:")
for drivetrain in unique_drivetrains:
    print(drivetrain)
# Doesn't need to be standardized, only a few values

# Verify that fuel_type is always Gasoline
print("\nSorted Unique Fuel Types:")
for fuel_type in unique_fuel_types:
    print(fuel_type)
# Only Gasoline, column can be removed.

Sorted Unique Engines:
-
1.0L I3 12V GDI DOHC Turbo
1.3L I3 12V GDI DOHC Turbo
1.3L I3 12V MPFI DOHC Turbo
1.3L I4 16V GDI SOHC Turbo
1.4L I-4 DOHC, variable valve control, regular unleaded, engine
1.4L I-4 gasoline direct injection, DOHC, variable valve control
1.4L I4
1.4L I4 16V GDI DOHC Turbo
1.4L I4 16V MPFI DOHC
1.4L I4 16V MPFI DOHC Turbo
1.4L I4 16V MPFI SOHC
1.4L I4 16V MPFI SOHC Turbo
1.4L TSI
1.5L EcoBoost
1.5L I-4 DOHC, variable valve control, regular unleaded, engine
1.5L I-4 gasoline direct injection, DOHC, VTEC variable valve co
1.5L I-4 gasoline direct injection, DOHC, VVT variable valve con
1.5L I-4 gasoline direct injection, DOHC, i-VTEC variable valve
1.5L I-4 gasoline direct injection, DOHC, variable valve control
1.5L I-4 variable valve control, regular unleaded, engine with 1
1.5L I3 12V GDI DOHC Turbo
1.5L I3 12V PDI DOHC Turbo
1.5L I4 16V GDI DOHC
1.5L I4 16V GDI DOHC Turbo
1.5L I4 16V MPFI SOHC
1.5L I4 DOHC 16V
1.5L I4 Turbocharged DOHC 16V LEV3-SULEV30 158hp
1

In [88]:
# isolate important engine attributes: 
# cylinders
# liters
# boosted T/F

import pandas as pd
import re
df = pd.read_csv('cars.csv')

# Define regular expressions for extracting attributes
#cylinders_pattern_1 = re.compile(r'(\d+)\s*Cyl')
cylinders_pattern_1 = re.compile(r'(\d+)[\s-]*Cyl')
#cylinders_pattern_2 = re.compile(r'[IVHW]-?([3-9]|1[0-2])')
cylinders_pattern_2 = re.compile(r'(?:[IVHW]|VR)-?([3-9]|1[0-2])')
liters_pattern_1 = re.compile(r'(\d+(?:\.\d+)?)L') # For cases like "3.6L"
liters_pattern_2 = re.compile(r'(\d+(?:\.\d+)?)\s*Liter') # For cases like "3.6 Liter"

boosted_pattern = re.compile(r'Turbo|Supercharge', re.IGNORECASE)

# Function to extract engine attributes
def extract_attributes(engine_str):
    # Extracting cylinders
    cylinders_match_1 = re.search(cylinders_pattern_1, engine_str)
    cylinders_match_2 = re.search(cylinders_pattern_2, engine_str)

    if cylinders_match_1:
        cylinders = cylinders_match_1.group(1)
    elif cylinders_match_2:
        cylinders = cylinders_match_2.group(1) or cylinders_match_2.group(2)
    else:
        cylinders = None

    
    #liters = re.search(liters_pattern, engine_str).group(1) if re.search(liters_pattern, engine_str) else None
    liters_match_1 = re.search(liters_pattern_1, engine_str)
    liters_match_2 = re.search(liters_pattern_2, engine_str)
    if liters_match_1:
        liters = liters_match_1.group(1)
    elif liters_match_2:
        liters = liters_match_2.group(1)
    else:
        liters = None

    # Handle the case where the liters are specified without 'L'
    if not liters and engine_str.replace('.', '', 1).isdigit():
        liters = engine_str

    boosted = bool(re.search(boosted_pattern, engine_str))
    
    return cylinders, liters, boosted

# Apply the function to the 'engine' column
df[['Cylinders', 'Liters', 'Boosted']] = df['engine'].apply(extract_attributes).apply(pd.Series)

# Display the resulting DataFrame
#pd.set_option('display.max_rows', None)
pd.reset_option('display.max_rows')
df[['engine', 'Cylinders', 'Liters', 'Boosted']]

engine Cylinders Liters  Boosted
0                2.4L I4 16V GDI DOHC         4    2.4    False
1                5.7L V8 16V MPFI OHV         8    5.7    False
2               1.6L I4 16V MPFI DOHC         4    1.6    False
3                5.7L V8 16V MPFI OHV         8    5.7    False
4               3.6L V6 24V MPFI DOHC         6    3.6    False
...                               ...       ...    ...      ...
5997             3.5L V6 24V PDI DOHC         6    3.5    False
5998            1.6L I4 16V MPFI DOHC         4    1.6    False
5999  3.5L V6 24V PDI DOHC Twin Turbo         6    3.5     True
6000             2.5L I4 16V GDI DOHC         4    2.5    False
6001       1.5L I4 16V GDI DOHC Turbo         4    1.5     True

[6002 rows x 4 columns]

In [89]:
# Display unique engines along with extracted attributes in a new DataFrame
unique_engines = df['engine'].unique()
engine_data = []

for engine in unique_engines:
    cylinders, liters, boosted = extract_attributes(engine)
    engine_data.append({'Engine': engine, 'Cylinders': cylinders, 'Liters': liters, 'Boosted': boosted})

engine_df = pd.DataFrame(engine_data)
#pd.set_option('display.max_rows', None)
pd.reset_option('display.max_rows')
engine_df

# Edge cases:
# row 295 "Electric"
# row 391 "-"

Engine Cylinders Liters  \
0                                 2.4L I4 16V GDI DOHC         4    2.4   
1                                 5.7L V8 16V MPFI OHV         8    5.7   
2                                1.6L I4 16V MPFI DOHC         4    1.6   
3                                3.6L V6 24V MPFI DOHC         6    3.6   
4                      3.0L V6 24V GDI DOHC Twin Turbo         6    3.0   
5                           2.0L I4 16V GDI DOHC Turbo         4    2.0   
6                                 2.5L I4 16V GDI DOHC         4    2.5   
7                                1.8L I4 16V MPFI SOHC         4    1.8   
8                                           4 Cylinder         4   None   
9                           3.0L I6 24V GDI DOHC Turbo         6    3.0   
10                               2.5L I4 16V MPFI DOHC         4    2.5   
11   4.7L V-8 gasoline direct injection, DOHC, vari...         8    4.7   
12                                 6.2L V8 16V GDI OHV         8    6.2   
13                                3.6L V6 24V GDI DOHC         6    3.6   
14                          1.5L I4 16V GDI DOHC Turbo         4    1.5   
15                               4.8L V8 32V MPFI DOHC         8    4.8   
16                               4.6L V8 24V MPFI SOHC         8    4.6   
17                               5.2L V10 40V GDI DOHC        10    5.2   
18   1.6L I-4 gasoline direct injection, DOHC, vari...         4    1.6   
19                   3.0L V6 24V GDI DOHC Supercharged         6    3.0   
20                               2.4L I4 16V MPFI SOHC         4    2.4   
21                          2.5L I4 16V PDI DOHC Turbo         4    2.5   
22                         2.5L H4 16V MPFI DOHC Turbo         4    2.5   
23                                2.0L H4 16V GDI DOHC         4    2.0   
24                                2.5L H4 16V GDI DOHC         4    2.5   
25                               2.5L H4 16V MPFI DOHC         4    2.5   
26   2L H-4 gasoline direct injection, DOHC, variab...         4      2   
27                               3.5L V6 24V MPFI DOHC         6    3.5   
28   3L V-6 gasoline direct injection, DOHC, variab...         6      3   
29                          2.0L I4 16V PDI DOHC Turbo         4    2.0   
30                     3.5L V6 24V GDI DOHC Twin Turbo         6    3.5   
31        560.0HP 4.4L 8 Cylinder Engine Gasoline Fuel         8    4.4   
32                         1.4L I4 16V MPFI DOHC Turbo         4    1.4   
33                               3.5L V6 24V MPFI SOHC         6    3.5   
34                               2.0L I4 16V MPFI DOHC         4    2.0   
35                               4.7L V8 32V MPFI DOHC         8    4.7   
36                               3.0L I6 24V MPFI DOHC         6    3.0   
37                         1.8L I4 20V MPFI DOHC Turbo         4    1.8   
38                               4.0L V6 24V MPFI SOHC         6    4.0   
39                          2.5L H4 16V GDI DOHC Turbo         4    2.5   
40                               4.4L V8 32V MPFI DOHC         8    4.4   
41                               4.2L V8 40V MPFI DOHC         8    4.2   
42                               4.0L V8 32V MPFI DOHC         8    4.0   
43                               2.3L I4 16V MPFI DOHC         4    2.3   
44                               3.8L V6 24V MPFI DOHC         6    3.8   
45                                3.9L V6 12V MPFI OHV         6    3.9   
46                                3.8L V6 12V MPFI OHV         6    3.8   
47                               3.0L V6 24V MPFI DOHC         6    3.0   
48                               4.7L V8 16V MPFI SOHC         8    4.7   
49                               4.2L I6 24V MPFI DOHC         6    4.2   
50                               5.0L V8 32V SPFI DOHC         8    5.0   
51                                4.3L V6 12V MPFI OHV         6    4.3   
52                                3.5L V6 12V MPFI OHV         6    3.5  

In [90]:
df.to_csv('new_cars.csv',index=False)